# L4: Syntactic Analysis

## Introduction

In this lab you will experiment with [MaltParser](http://www.maltparser.org/), a standard tool for syntactic analysis.

Syntactic analysis, also called syntactic parsing, is the task to map a sentence to a representation of its syntactic structure. In this lab you will work with syntactic structures in the form of **dependency trees**. A dependency tree consists of directed arcs between individual words (tokens) of a sentence. A realistic example of how such a tree can look like is shown below. The tree shown is the first dependency tree from the test set of the [Swedish Treebank](https://stp.lingfil.uu.se/~nivre/swedish_treebank/).

![Figur 1](https://www.ida.liu.se/~729G17/commons/dep_tree.png)

Every arc in a dependency tree links two words: the word the arc points to is called **dependent**; the word at the source of the arc is called **head**. In the example *pensionen* is the dependent to *är* and, at the same time, the head of *den* and *allmäna*. Every word except the special root word has exactly one head. The root word does not have a head (but it can have dependents). In the example tree, the word *är* is the tree's root, marked with a special arc.

The arcs in a dependency tree are often labelled with **grammatical relations**. In the tree above, the arc from *är* to *pensionen* is labelled with the grammatical relation `SS`, expressing that *pensionen* functions as the grammatical subject to its head word *är*. More information on which grammtical relations are used in the Swedish Treebank can be found [here](https://stp.lingfil.uu.se/~nivre/swedish_treebank/GF.html).

As usual we start by loading the Python module needed for this lab:

In [ ]:
import lt4

## Evaluation

In the first part of the lab, your task is to evaluate dependency parsers, something that is relevant if you for example want to compare various parsers. Four standard measures are used for the evaluation:

**unlabelled attachment score (UAS)**<br/>the percentage of words in the test set that were attached to their correct heads (as specified in the gold standard)

**labelled attachment score (LAS)**<br/>the percentage of words that were attached to their correct heads *and* assigned the correct dependency relation

**unlabelled exact match (UEM)**<br/>the percentage of sentences in which every word was attached to its correct head

**labelled exact match (LEM)**<br/>the percentage of sentences in which every word was attached to its correct head *and* assigned the correct dependency relation

Thus every word/sentence the parser gets credit for under the labelled measures, it also gets credit for under the unlabelled measures, but not vice versa.

### First steps with MaltParser

Before you do anything else, start reading the [MaltParser User Guide](http://maltparser.org/userguide.html), beginning with *Start Using MaltParser* which consists of *Train a parsing model* and *Parse data with your parsing model*. This section explains how you train a parsing model on gold-standard data and how you then use the model to parse new text. Your first task is to execute these two steps with the data from the Swedish Treebank. The data is divided into two files in the directory `/courses/729G17/labs/l4/data/`:

|   data type   | filename                     | sentences |
|---------------|------------------------------|-----------|
| training data | `talbanken-dep-train.conll`  |      4941 |
| test data     | `talbanken-dep-test.conll`   |      1219 |

<div class="panel panel-primary">
<div class="panel-heading">Problem 1</div>
<div class="panel-body">
    
Train a parsing model on the training data and use it to parse the sentences in the test data. Follow the instructions in the [MaltParser User Guide](http://maltparser.org/userguide.html). Put your output file in the same directory as this notebook and name it `out.conll`. Evaluate the parser by calculating the four evaluation measures LAS, UAS, LEM, UEM.
</div>
</div>

The file  `maltparser-1.9.2.jar` can be found in the directory `/courses/729G17/labs/l4/maltparser-1.9.2`.

<div class="alert alert-warning">
Note that MaltParser is a Java program you are supposed to run from the terminal!
</div>

Load the test data and the parser&rsquo;s output data by running the next code cell:

In [ ]:
# The gold-standard test data
test_data = lt4.read_data("/courses/729G17/labs/l4/data/talbanken-dep-test.conll")

# The parser output
# TODO: Change the path once you have produced the file out.conll!
out_data = lt4.read_data("/courses/729G17/labs/l4/data/dummy.conll")
#out_data = lt4.read_data("out.conll")

Evaluate the parser by running the codecell below:

In [ ]:
print("LAS: {:.2%}".format(lt4.las(test_data, out_data)))
print("UAS: {:.2%}".format(lt4.uas(test_data, out_data)))
print("LEM: {:.2%}".format(lt4.lem(test_data, out_data)))
print("UEM: {:.2%}".format(lt4.uem(test_data, out_data)))

### Draw your own dependency tree

In order to better understand the dependency parsing task and how to interpret the data, it might help to draw a dependency tree by hand.

#### Representation of dependency trees in the data

The files from the Swedish Treebank follow the so called CoNLL-format, which essentially stores information about sentences as [tab-separated values](https://en.wikipedia.org/wiki/Tab-separated_valuestab-separed). We can thus view every sentence as a table. Every row in this table correspond to a word, and every column contains a specific type of information about that word &ndash; column&nbsp;2 e.g. contains the word form, column&nbsp;4 contains the word&rsquo;s POS tag, etc. The table for the example tree from above looks like this:

| position | word form | (not used) | fine-grained POS | coarse-grained POS | morphological features | head | grammatical relation |
|---|---|---|---|---|---|---|---|
|1 | Den | _ | DT | DT | UTR&#124;SIN&#124;DEF | 3 | DT |
|2 | allmänna | _ | JJ | JJ | POS&#124;UTR/NEU&#124;SIN&#124;DEF&#124;NOM | 3 | AT |
|3 | pensionen | _ | NN | NN | UTR&#124;SIN&#124;DEF&#124;NOM | 4 | SS |
|4 | är | _ | VB | VB | PRS&#124;AKT | 0 | ROOT |
|5 | av | _ | PP | PP | _ | 4 | SP |
|6 | två | _ | RG | RG | NOM | 7 | DT |
|7 | slag | _ | NN | NN | NEU&#124;PLU&#124;IND&#124;NOM | 5 | PA |
|8 | : | _ | MID | MID | _ | 7 | IQ |
|9 | folkpension | _ | NN | NN | UTR&#124;SIN&#124;IND&#124;NOM | 10 | CJ |
|10 | och | _ | KN | KN | _ | 7 | AN |
|11 | tilläggspension | _ | NN | NN | UTR&#124;SIN&#124;IND&#124;NOM | 10 | CJ |
|12 | ( | _ | PAD | PAD | _ | 11 | IR |
|13 | ATP | _ | PM | PM | NOM | 11 | AN |
|14 | ) | _ | PAD | PAD | _ | 11 | JR |
|15 | . | _ | MAD | MAD | _ | 4 | IP |

#### Representation of a dependency tree in Python

When you read in dependency trees using the function `read_data()`, you are given every tree as a list of lists, where the inner lists correspond to the word lines, and the elements of the inner lists correspond to the columns. The cell below shows how to print the inner lists of the example sentence.

In [ ]:
sample_tree = test_data[0]

for row in sample_tree:
    print(row)

<div class="panel panel-primary">
<div class="panel-heading">Problem 2</div>
<div class="panel-body">
Draw the tree with index 58 in the test data in the format you know from the lectures and the picture above.
</div>
</div>

The easiest way to solve this problem is to draw the tree on a piece of paper, and attach a photo or scan of the tree in your submission. Use the next code cell to print the tree.

In [ ]:
# TODO: Print the tree with index 58 in the test data

### Implement the evaluation measures

Your next task is to implement the four evaluation measures.

<div class="panel panel-primary">
<div class="panel-heading">Problem 3</div>
<div class="panel-body">
Write your own implementations of the four evaluation measures. Redo the evaluation that you did in Problem&nbsp;1 with your own implementations to check whether your code is working as expected.
</div>
</div>

To solve this problem you should change the function definitions in the following code cell. Every function expects two arguments; a list containing the gold-standard trees (`gold_trees`) and a matching list with the predicted trees (`pred_trees`). Every function should then return the respective measure as a floating-point number between 0&nbsp;and&nbsp;1; if the measure is not defined, it should return `float('NaN')`. For now the functions simply call their respective counterparts from the lab module `lt4`; replace these calls with your own code.

In [ ]:
def las(gold_trees, pred_trees):
    """Computes Labelled Attachment Score (LAS)"""
    # TODO: Replace the following line with your own code to solve Problem 2.
    return lt4.las(gold_trees, pred_trees)

def uas(gold_trees, pred_trees):
    """Computes Unlabelled Attachment Score (UAS)"""
    # TODO: Replace the following line with your own code to solve Problem 2.
    return lt4.uas(gold_trees, pred_trees)

def lem(gold_trees, pred_trees):
    """Computes Labelled Exact Match (LEM)"""
    # TODO: Replace the following line with your own code to solve Problem 2.
    return lt4.lem(gold_trees, pred_trees)

def uem(gold_trees, pred_trees):
    """Computes Unlabelled Exact Match (UEM)"""
    # TODO: Replace the following line with your own code to solve Problem 2.
    return lt4.uem(gold_trees, pred_trees)

To implement the four functions you will have to extract and compare the relevant information from the gold-standard and the predicted trees. The following code cell illustrates how you can get this information. Remember that Python&rsquo;s indexing starts at&nbsp;0.

In [ ]:
sample_tree = test_data[0]

print(sample_tree[2][1]) # word 3 (pensionen), word form (column 2)
print(sample_tree[3][3]) # word 4 (är), fine-grained POS (column 4)
print(sample_tree[2][6]) # word 3 (pensionen), position of the word's head (column 7)
print(sample_tree[2][7]) # word 3 (pensionen), dependency relation with the head (column 8)

<div class="alert alert-warning">
Note that the root word is marked by having position&nbsp;0 as its head, which does not have a corresponding word in the sentence.
</div>

Test your implementation by running the following:

In [ ]:
print("LAS: {:.2%}".format(las(test_data, out_data)))
print("UAS: {:.2%}".format(uas(test_data, out_data)))
print("LEM: {:.2%}".format(lem(test_data, out_data)))
print("UEM: {:.2%}".format(uem(test_data, out_data)))

### Reflect on the measures

In the next problem your task is to reflect on the evaluation you did in the previous exercise.

<div class="panel panel-primary">
<div class="panel-heading">Problem 4</div>
<div class="panel-body">
    
Suppose that you want to build a system that finds all instances of a person executing a certain action in a large set of sentences, e.g. &lsquo;write a book&rsquo; or &lsquo;buy a car&rsquo;. Argue why in this scenario, *attachment score* may be a more suitable evaluation metric than *exact match*.
</div>
</div>

*TODO: Write your answer for Problem 4 here*

## Experiment with predicted tags

Most syntactic dependency parsers require input data that has been POS-tagged, and MaltParser is no exception. The test data you have used so far contains gold-standard tags, making the evaluation somewhat misleading: In a practical system, one usually does not have access to gold-standard tags; instead one has to first tag the sentences with an automatic POS tagger (for example the one you used in lab&nbsp;L3).

<div class="panel panel-primary">
<div class="panel-heading">Problem 5 (Reflection)</div>
<div class="panel-body">
    <p>Set up an experiment to find out what type of parser performs better when parsing automatically POS-tagged data:</p>
    <ul>
        <li>A: a parser trained on gold-standard tags (like the one in Problem&nbsp;1); or</li>
        <li>B: a parser where even the training data was automatically tagged.</li>
    </ul>
    <p>Write a short reflection piece about your experience. Use the following prompts:</p>
    <ul>
        <li>How did you set up the experiment? What were the results?</li>
        <li>Based on your previous knowledge, did you expect the results? How do you explain them?</li>
        <li>What did you learn from this experiment? How, exactly, did you learn it? Why does this learning matter?</li>
    </ul>
</div>
</div>

Automatically tagged training and test data can be found in the directory `/courses/729G17/labs/l4/data/`:

|              .                | filename                         | sentences |
|-------------------------------|----------------------------------|-----------|
| training data (auto-tagged)   | `talbanken-dep-train-auto.conll` |      4941 |
| test data (auto-tagged)       | `talbanken-dep-test-auto.conll`  |      1219 |

*TODO: Insert your text for Problem 5 here*

<div class="alert alert-info">
    Do not forget to read the General Information section on the lab web page before submitting this notebook!
</div>